Assessment Requirements 
Each group is required to complete the following two tasks: 
1. Generate a sparse representation for Paper Bodies (i.e. paper text without Title, Authors, Abstract and References). The sparse representation consists of two files: a. Vocabulary index file b. Sparse count vectors file 
 
2. Generate  a CSV file (stats.csv) containing three columns: a. Top 10 most frequent terms appearing in all Titles b. Top 10 most frequent Authors c. Top 10 most frequent terms appearing in all Abstracts 
 
Note: In case of ties in any of the above fields, settle the tie based on alphabetical ascending order. (example:  if the author named John appeared as many times as Mark, then John shall be selected over Mark) 

In [1]:
import re
import pandas
import requests
import os
import pdfminer
import tqdm
from tqdm import tqdm_notebook as tqdm

# segmentation first, then find capital words, then loop through and lower each word, then tokenize.
import io
from io import StringIO
from pdfminer.pdfinterp import PDFResourceManager, PDFPageInterpreter
from pdfminer.converter import TextConverter
from pdfminer.layout import LAParams
from pdfminer.pdfpage import PDFPage
import os
import sys, getopt

import nltk.data
sent_detector = nltk.data.load('tokenizers/punkt/english.pickle')

from nltk.collocations import BigramCollocationFinder 
from nltk.metrics import BigramAssocMeasures
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from nltk.tokenize import MWETokenizer
from itertools import chain
from sklearn.feature_extraction.text import TfidfVectorizer

from nltk.tokenize import RegexpTokenizer
from nltk.tokenize import MWETokenizer


from nltk.probability import *
from nltk.tokenize import word_tokenize


from nltk.collocations import BigramCollocationFinder 
from nltk.metrics import BigramAssocMeasures
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from nltk.tokenize import MWETokenizer
from itertools import chain
from sklearn.feature_extraction.text import TfidfVectorizer

from nltk.stem.porter import *
nltk.download('punkt')

ModuleNotFoundError: No module named 'pdfminer'

In [ ]:
!pip install Tabula-py 
!pip install pdfminer.six 
!pip install pdfminer3k 
!pip install tqdm
!pip install pdfminer
#pdfminer3k is a Python 3 port of pdfminer

In [5]:
import tabula
# readinf the PDF file that contain Table Data
# you can find find the pdf file with complete code in below
# read_pdf will save the pdf table into Pandas Dataframe
df = tabula.read_pdf("Group102.pdf")
# in order to print first 5 lines of Table
df.head()

filename                                                url
0  PP3265.pdf  https://drive.google.com/uc?export=download&id...
1  PP3284.pdf  https://drive.google.com/uc?export=download&id...
2  PP3316.pdf  https://drive.google.com/uc?export=download&id...
3  PP3369.pdf  https://drive.google.com/uc?export=download&id...
4  PP3382.pdf  https://drive.google.com/uc?export=download&id...

In [6]:
if not os.path.exists('data'):
    os.makedirs('data') # make a dataset, to store all the pdf files downloaded
    for each in tqdm(df.iterrows()):
        response = requests.get(each[1][1])
        with open('data/'+ str(each[1][0]),'wb') as f:
            f.write(response.content)

In [7]:

#converts pdf, returns its text content as a string
def convert(fname, pages=None):
    if not pages:
        pagenums = set()
    else:
        pagenums = set(pages)

    output = io.StringIO()
    manager = PDFResourceManager()
    converter = TextConverter(manager, output, laparams=LAParams())
    interpreter = PDFPageInterpreter(manager, converter)

    infile = open(fname, 'rb')
    for page in PDFPage.get_pages(infile, pagenums):
        interpreter.process_page(page)
    infile.close()
    converter.close()
    text = output.getvalue()
    output.close
    return text 

#converts all pdfs in directory pdfDir, saves all resulting txt files to txtdir
def convertMultiple(pdfDir, txtDir):
    if pdfDir == "": pdfDir = os.getcwd() + "\\" #if no pdfDir passed in 
    for pdf in tqdm(os.listdir(pdfDir)): #iterate through pdfs in pdf directory
        fileExtension = pdf.split(".")[-1]
        if fileExtension == "pdf":
            pdfFilename = pdfDir + pdf 
            text = convert(pdfFilename) #get string of text content of pdf
            textFilename = txtDir + pdf + ".txt"
            textFile = open(textFilename, "w") #make text file
            textFile.write(text) #write text to text file

# set paths accordingly:
pdfDir = "C:/your_path_here/"
txtDir = "C://your_path_here/"

In [8]:
# segmentation first, then find capital words, then loop through and lower each word, then tokenize.
import io
from io import StringIO
from pdfminer.pdfinterp import PDFResourceManager, PDFPageInterpreter
from pdfminer.converter import TextConverter
from pdfminer.layout import LAParams
from pdfminer.pdfpage import PDFPage
import os
import sys, getopt

import nltk.data
sent_detector = nltk.data.load('tokenizers/punkt/english.pickle')

In [9]:
# re.findall(r'(?<!^)(?<!\. )[A-Z][a-z]+',mystr) #regex is to find the capitalized words in the middle of the sentence

In [10]:
def selective_lower(sentence): #E
    aux_sentence = ''
    cap_set = re.findall(r'(?<!^)(?<!\. )[A-Z][a-z]+',sentence) #A.
    
    sentence = sentence.replace('- ','')

    for word in sentence.split(" "):
        if word not in cap_set:
            aux_sentence += word.lower() + str(' ')
        else:
            aux_sentence += word + str(' ')

    return aux_sentence.strip()

In [11]:
tokenizer = RegexpTokenizer("[A-Za-z]\w+(?:['?]\w+)?")

In [12]:
import os
from tqdm import tqdm

sent_detector = nltk.data.load('tokenizers/punkt/english.pickle')
body_dict={}

def get_data(directory):
        
    body_dict={}   
    for filename in tqdm(os.listdir(directory)):
            filepdf = filename.replace('.pdf','')
            raw_body = convert(str(os.path.join(directory, filename)))
                     
            sentence_list = sent_detector.tokenize(raw_body.strip())

            body = []
            start = 0
            stop = 0
            for i in range(len(sentence_list)):
                if 'Paper Body' in sentence_list[i]:
                    start = i
                if '2 Reference' in sentence_list[i]:
                    stop = i
                sentence_list[i] = sentence_list[i].replace('w indows','windows')
                sentence_list[i] = sentence_list[i].replace('W indows','Windows')
            # this is to find the start and stop of Paper body
            for i in range(start, stop):
                body.append(sentence_list[i])
            for i in range(len(body)):
                body[i] = body[i].replace('\n',' ') #replace all the new line
                body[i] = selective_lower(body[i]) #E:.
                
                temp_list = []
                l = body[i].split()

                        
                count_2letter_words = 1
                while count_2letter_words > 0:
                    for word in l:
                        if len(word) < 3:
                            l.remove(word)
                    count_2letter_words = 0
                    for word in l:
                        if len(word) < 3:
                            count_2letter_words += 1
                            break   
                            
                for tok in l:
                    temp_list.append(tok)
            
                        
                temp_string = " ".join(temp_list)
                body[i] = temp_string
                
                
            body_dict[filepdf] = " ".join(body)
            shortword = re.compile(r'\W*\b\w{1,2}\b')
            body_dict[filepdf] = shortword.sub('',body_dict[filepdf])
    return body_dict


In [13]:
pathpdf = 'data/'
body_dict = get_data(pathpdf)

100%|██████████████████████████████████████████████████████████████████████████████████| 49/49 [00:47<00:00,  1.01it/s]


In [14]:
shortword = re.compile(r'\W*\b\w{1,2}\b')
for file in list(body_dict.keys()):
    body_dict[file] = shortword.sub('',body_dict[file])

In [19]:
def tokenize(body):
    tokenized_body = tokenizer.tokenize(body_dict[body]) #tokenizing the string
    return (body, tokenized_body) # return a tuple of file name and a list of tokens

#calling the tokenize method in a loop for all the elements in the dictionary
tokenized_body = dict(tokenize(body) for body in body_dict.keys()) 

In [20]:
#An empty list to store all the given stopwords
stopwords=[]

#Opening the given stopwords file and storing the words in the stopwords list
with open('stopwords_en.txt') as f:
    stopwords = f.read().splitlines()    

In [ ]:
all_tokens

In [21]:
from itertools import chain
all_tokens = list(chain.from_iterable(tokenized_body.values())) 

#remove context dependent stopwords D. B.
vectorizer = CountVectorizer(input = 'content', analyzer = 'word',max_df=0.95, min_df=0.03)
vectorizerobject = vectorizer.fit_transform(all_tokens)

In [22]:
#remove context independent stopwords and 2 letter
count = 1
while count > 0:
    for word in all_tokens:
        if (len(word) < 3) or (word in stopwords) or (word == 'The'):
            all_tokens.remove(word)
    count = 0
    for word in all_tokens:
        if (len(word) < 3) or (word in stopwords) or (word == 'The'): #F D. B.
            count += 1
            break   
#double check
for word in all_tokens:
    if len(word) < 3:
        print(word)

In [ ]:
all_tokens

In [23]:
#Finding the top 200 bigrams
finder=BigramCollocationFinder.from_words(all_tokens)
bigrams=finder.nbest(BigramAssocMeasures.likelihood_ratio, 200)
bigrams_list=[x for x in bigrams if not any(c.isdigit() for c in x)] 

In [ ]:
bigrams_list

In [24]:
#Eliminating numbers from bigrams
bigrams_list=[x for x in bigrams if not any(c.isdigit() for c in x)] 

In [ ]:
type(bigrams_list[1])

In [25]:
bigrams_list

[('Paper', 'Body'),
 ('ground', 'truth'),
 ('roc', 'curve'),
 ('nearest', 'neighbor'),
 ('distributionally', 'robust'),
 ('supplementary', 'material'),
 ('training', 'set'),
 ('Rand', 'index'),
 ('sequentially', 'robust'),
 ('state', 'art'),
 ('unlabeled', 'data'),
 ('soft', 'cascade'),
 ('monotone', 'submodular'),
 ('spike', 'sorting'),
 ('cross', 'validation'),
 ('aﬃnity', 'graph'),
 ('data', 'sets'),
 ('log', 'log'),
 ('Markov', 'chain'),
 ('upper', 'bound'),
 ('tdb', 'lasso'),
 ('objective', 'function'),
 ('asymptotic', 'variance'),
 ('reinforcement', 'learning'),
 ('matrix', 'completion'),
 ('text', 'categorization'),
 ('optimization', 'problem'),
 ('Gaussian', 'process'),
 ('lower', 'bound'),
 ('low', 'rank'),
 ('machine', 'learning'),
 ('tabular', 'reedy'),
 ('roc', 'curves'),
 ('hinge', 'loss'),
 ('jitter', 'strength'),
 ('exponential', 'family'),
 ('dual?rpr', 'dual?rpr'),
 ('norm', 'mkl'),
 ('lattice', 'regression'),
 ('gradient', 'descent'),
 ('rpr', 'Pexplore'),
 ('time', '

In [26]:
#Preserving these bigrams and putting it back in the dictionary, along with the unigrams
mwetokenizer = MWETokenizer(bigrams_list,separator='__')

In [27]:
#remove context independent stopwords and 2 letter
for file in list(tokenized_body.keys()):
    count = 1
    while count > 0:
        for word in tokenized_body[file]:
            if (len(word) < 3) or (word in stopwords) or (word == 'The'):
                tokenized_body[file].remove(word)
        count = 0
        for word in tokenized_body[file]:
            if (len(word) < 3) or (word in stopwords) or (word == 'The'): #F D. B.
                count += 1
                break   
#double check
for file in list(tokenized_body.keys()):
    for word in tokenized_body[file]:
        if len(word) < 3:
            print(word)

In [28]:
#colloc_body is a dictionary that contains both the bigrams as well as the unigrams
colloc_body =  dict((body, mwetokenizer.tokenize(data)) for body,data in tokenized_body.items())

In [29]:
colloc_body # ABDEF

{'PP3265': ['Paper__Body',
  'state__art',
  'real',
  'time',
  'face',
  'detection',
  'progressed',
  'rapidly',
  'recently',
  'years',
  'successful',
  'approach',
  'initiated',
  'Viola',
  'Jones',
  'components',
  'work',
  'simple',
  'called',
  'integral',
  'image',
  'adaboost',
  'great',
  'deal',
  'complexity',
  'lies',
  'training',
  'cascaded',
  'detector',
  'required',
  'parameters',
  'number',
  'shapes',
  'rectangle',
  'lters',
  'number',
  'stages',
  'number',
  'weak__classiﬁers',
  'stage',
  'target',
  'detection__rate',
  'cascade',
  'stage',
  'parameters',
  'conspire',
  'determine',
  'roc__curve',
  'resulting',
  'system',
  'computational__complexity',
  'viola',
  'jones',
  'training',
  'process',
  'requires',
  'cpu',
  'days',
  'train',
  'evaluate',
  'diﬃcult',
  'impossible',
  'pick',
  'parameters',
  'optimally',
  'conceptual',
  'computational__complexity',
  'training',
  'process',
  'led',
  'papers',
  'proposing',
 

In [ ]:
#for file in list(tokenized_body.keys()):
#        count = 1
#        while count > 0:
#            for word in tokenized_body[file]:
#                if (len(word) < 3) or (word in stopwords) :
#                    tokenized_body[file].remove(word)
#            count = 0
#            for word in tokenized_body[file]:
#                if (len(word) < 3) or (word in stopwords):
#                    count += 1
#                    break   
#double check
#for file in list(tokenized_body.keys()):
#    for word in tokenized_body[file]:
#        if len(word) < 3:
#            print(word)
#            
# up to this point, tokenized body was cleanned from 2 letter word and stopwords

In [ ]:
#for file in list(tokenized_body.keys()):
# Using count vectorizer to remove words that occur in more than 95% and less than 3% of the vocab
#    vectorizer = CountVectorizer(input = 'content', analyzer = 'word',max_df=0.95, min_df=0.03)
#    vectorizerobject = vectorizer.fit_transform(tokenized_body[file])
#    tokenized_body[file] = vectorizer.get_feature_names()

In [30]:
colloc_body

{'PP3265': ['Paper__Body',
  'state__art',
  'real',
  'time',
  'face',
  'detection',
  'progressed',
  'rapidly',
  'recently',
  'years',
  'successful',
  'approach',
  'initiated',
  'Viola',
  'Jones',
  'components',
  'work',
  'simple',
  'called',
  'integral',
  'image',
  'adaboost',
  'great',
  'deal',
  'complexity',
  'lies',
  'training',
  'cascaded',
  'detector',
  'required',
  'parameters',
  'number',
  'shapes',
  'rectangle',
  'lters',
  'number',
  'stages',
  'number',
  'weak__classiﬁers',
  'stage',
  'target',
  'detection__rate',
  'cascade',
  'stage',
  'parameters',
  'conspire',
  'determine',
  'roc__curve',
  'resulting',
  'system',
  'computational__complexity',
  'viola',
  'jones',
  'training',
  'process',
  'requires',
  'cpu',
  'days',
  'train',
  'evaluate',
  'diﬃcult',
  'impossible',
  'pick',
  'parameters',
  'optimally',
  'conceptual',
  'computational__complexity',
  'training',
  'process',
  'led',
  'papers',
  'proposing',
 

In [69]:
#Using the porterstemmer method
ps = PorterStemmer()
#An empty string to store the content of a particular resume
strcontent=''
#An empty dictionary to append the stemmed data back 
stemmed_dict=dict()

#Looping to stem each value in the dictionary
for key,body in colloc_body.items():  
    for word in body:
        if (word[0].islower()) and ('__' not in word):
        #Temporarily storing the data in an empty string
            strcontent=strcontent+ ' ' + ps.stem(word)
    
    #Assigning the string to the respective key
    stemmed_dict[key]=strcontent
    #Again emptying the string to store the next resume
    strcontent=''

#Loop to again word tokenize each body in the dictionary and assigning it back to its body number 
for key,body in stemmed_dict.items():
    stemmed_dict[key]=word_tokenize(body)

In [32]:
stemmed_dict['']

{'PP3265': ['real',
  'time',
  'face',
  'detect',
  'progress',
  'rapidli',
  'recent',
  'year',
  'success',
  'approach',
  'initi',
  'compon',
  'work',
  'simpl',
  'call',
  'integr',
  'imag',
  'adaboost',
  'great',
  'deal',
  'complex',
  'lie',
  'train',
  'cascad',
  'detector',
  'requir',
  'paramet',
  'number',
  'shape',
  'rectangl',
  'lter',
  'number',
  'stage',
  'number',
  'stage',
  'target',
  'cascad',
  'stage',
  'paramet',
  'conspir',
  'determin',
  'result',
  'system',
  'viola',
  'jone',
  'train',
  'process',
  'requir',
  'cpu',
  'day',
  'train',
  'evalu',
  'diﬃcult',
  'imposs',
  'pick',
  'paramet',
  'optim',
  'conceptu',
  'train',
  'process',
  'led',
  'paper',
  'propos',
  'improv',
  'reﬁnement',
  'paper',
  'xiao',
  'zhang',
  'mata',
  'brandt',
  'paper',
  'origin',
  'cascad',
  'structur',
  'distinct',
  'separ',
  'stage',
  'relax',
  'earlier',
  'comput',
  'weak',
  'classiﬁ',
  'score',
  'combin',
  'bourdev'

In [74]:
for file in list(stemmed_dict.keys()):
    for word in colloc_body[file]:
        if (word[0].isupper()) or ('__' in word):
            stemmed_dict[file].append(word)

In [78]:
stemmed_dict['PP3265'].sort()

In [109]:
for i in stemmed_dict['PP3265']:
    if i == '?':
        print(i)

In [86]:
all_tok_cleaned = list(chain.from_iterable(stemmed_dict.values()))
all_tok_cleaned.sort()

In [87]:
_vocab = dict((x,all_tok_cleaned.count(x)) for x in set(all_tok_cleaned))

In [103]:
for i in stemmed_dict.values():
    if i == '?':
        print(i)

In [106]:
chain.from_iterable(stemmed_dict.values())

In [104]:
stemmed_dict.values()

dict_values([['Adaboost', 'Approach', 'Boosting', 'Bootstrapping', 'Bourdev', 'Brandt', 'Brandt', 'Cascade', 'Conclusions', 'Cumulative', 'Detection', 'Detection', 'Experimental', 'False', 'False', 'Feature', 'Figure', 'Figure', 'Figure', 'Figure', 'Figure', 'Figure', 'Figure', 'Figure', 'Figure', 'Figure', 'Figure', 'Final', 'Final', 'Final', 'For', 'For', 'For', 'Haar', 'Hastie', 'Index', 'Input', 'Input', 'Instance', 'Jones', 'Learn', 'Learning', 'More', 'Multiple', 'Negative', 'Nowlan', 'Number', 'Opteron', 'Paper__Body', 'Performance', 'Platt', 'Pos', 'Positive', 'Positive', 'Positive', 'Positive', 'Positive', 'Pruning', 'Pruning', 'Pruning', 'Rate', 'Rate', 'Rejection', 'Results', 'Results', 'Score', 'Section', 'Section', 'Slowness', 'Sochman', 'Sochman', 'Soft', 'Soft', 'Threshold', 'Threshold', 'Tibshirani', 'Traces', 'Trimming', 'Using', 'Viola', 'Weak', 'Weight', 'Windows', 'Windows', 'Zhang', 'Zhang', 'Zhu', 'absenc', 'accept', 'accept', 'accept', 'accept', 'accept', 'accept